# Installing and imports

In [ ]:
#clone YOLOv5 and 
!git clone https://github.com/ultralytics/yolov5  # clone repo
%cd yolov5
%pip install -qr requirements.txt # install dependencies
%pip install -q roboflow

import torch
import os
from IPython.display import Image, clear_output  # to display images

print(f"Setup complete. Using torch {torch.__version__} ({torch.cuda.get_device_properties(0).name if torch.cuda.is_available() else 'CPU'})")

Cloning into 'yolov5'...
remote: Enumerating objects: 13969, done.
remote: Counting objects: 100% (254/254), done.
remote: Compressing objects: 100% (114/114), done.
remote: Total 13969 (delta 162), reused 208 (delta 140), pack-reused 13715
Receiving objects: 100% (13969/13969), 13.35 MiB | 29.79 MiB/s, done.
Resolving deltas: 100% (9613/9613), done.
/content/yolov5
     |████████████████████████████████| 1.6 MB 4.9 MB/s 
     |████████████████████████████████| 1.1 MB 7.9 MB/s 
     |████████████████████████████████| 67 kB 6.0 MB/s 
     |████████████████████████████████| 145 kB 57.1 MB/s 
     |████████████████████████████████| 178 kB 63.4 MB/s 
     |████████████████████████████████| 138 kB 66.6 MB/s 
     |████████████████████████████████| 54 kB 3.4 MB/s 
     |████████████████████████████████| 62 kB 992 kB/s 
Setup complete. Using torch 1.12.1+cu113 (Tesla T4)


# Unzip directory with 640 training, 160 val and 200 test data

In [ ]:
!unzip "/content/drive/MyDrive/yolo_datasets/datasets_Train640_Val160_Test200.zip" -d "/content"


Archive:  /content/drive/MyDrive/yolo_datasets/datasets_Train640_Val160_Test200.zip
   creating: /content/datasets_Train640_Val160_Test200/AIROGS/
  inflating: /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml  
   creating: /content/datasets_Train640_Val160_Test200/AIROGS/test/
   creating: /content/datasets_Train640_Val160_Test200/AIROGS/test/images/
  inflating: /content/datasets_Train640_Val160_Test200/AIROGS/test/images/SHUF00800.png  
  inflating: /content/datasets_Train640_Val160_Test200/AIROGS/test/images/SHUF00801.png  
  inflating: /content/datasets_Train640_Val160_Test200/AIROGS/test/images/SHUF00802.png  
  inflating: /content/datasets_Train640_Val160_Test200/AIROGS/test/images/SHUF00803.png  
  inflating: /content/datasets_Train640_Val160_Test200/AIROGS/test/images/SHUF00804.png  
  inflating: /content/datasets_Train640_Val160_Test200/AIROGS/test/images/SHUF00805.png  
  inflating: /content/datasets_Train640_Val160_Test200/AIROGS/test/images/SHUF00806.png  
  infl

# Baseline - Train YOLOv5l model with auto batch size and default number of epochs 

In [ ]:
!python train.py --img 640 --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --weights yolov5l.pt --cache

train: weights=yolov5l.pt, cfg=, data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=300, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=100, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl

## Save results baseline model 

In [ ]:
# Save results
!cp -r "/content/yolov5/runs/train/exp" "/content/drive/MyDrive/yolo_datasets/baseline_small_training_set"

## Get metric results test data

In [ ]:
!python val.py --weights /content/drive/MyDrive/yolo_datasets/baseline_small_training_set/exp/weights/best.pt --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --task test

val: data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, weights=['/content/drive/MyDrive/yolo_datasets/baseline_small_training_set/exp/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

Fusing layers... 
Model summary: 267 layers, 46113663 parameters, 0 gradients, 107.7 GFLOPs
test: Scanning '/content/datasets_Train640_Val160_Test200/AIROGS/test/labels' images and labels...200 found, 0 missing, 0 empty, 0 corrupt: 100% 200/200 [00:00<00:00, 382.62it/s]
test: New cache created: /content/datasets_Train640_Val160_Test200/AIROGS/test/labels.cache
                 Class     Images  Instances          P          R      mAP50   mAP50-95: 100%

# Trying out model sizes

## Nano

In [ ]:
!python train.py --img 640 --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --weights yolov5n.pt --patience 20 --cache

train: weights=yolov5n.pt, cfg=, data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=300, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=20, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl_

In [ ]:
!cp -r "/content/yolov5/runs/train/exp2" "/content/drive/MyDrive/yolo_datasets/Model_sizes_results/nano"

In [ ]:
!python val.py --weights /content/drive/MyDrive/yolo_datasets/Model_sizes_results/nano/exp2/weights/best.pt --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --task test

val: data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, weights=['/content/drive/MyDrive/yolo_datasets/Model_sizes_results/nano/exp2/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

Fusing layers... 
Model summary: 157 layers, 1761871 parameters, 0 gradients, 4.1 GFLOPs
test: Scanning '/content/datasets_Train640_Val160_Test200/AIROGS/test/labels.cache' images and labels... 200 found, 0 missing, 0 empty, 0 corrupt: 100% 200/200 [00:00<?, ?it/s]
                 Class     Images  Instances          P          R      mAP50   mAP50-95: 100% 7/7 [00:05<00:00,  1.39it/s]
                   all        200        400      0.975      0.964   

## Small

In [ ]:
!python train.py --img 640 --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --weights yolov5s.pt --patience 20 --cache

train: weights=yolov5s.pt, cfg=, data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=300, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=20, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl_

In [ ]:
!cp -r "/content/yolov5/runs/train/exp3" "/content/drive/MyDrive/yolo_datasets/Model_sizes_results/small"

In [ ]:
!python val.py --weights /content/drive/MyDrive/yolo_datasets/Model_sizes_results/small/exp3/weights/best.pt --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --task test

val: data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, weights=['/content/drive/MyDrive/yolo_datasets/Model_sizes_results/small/exp3/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

Fusing layers... 
Model summary: 157 layers, 7015519 parameters, 0 gradients, 15.8 GFLOPs
test: Scanning '/content/datasets_Train640_Val160_Test200/AIROGS/test/labels.cache' images and labels... 200 found, 0 missing, 0 empty, 0 corrupt: 100% 200/200 [00:00<?, ?it/s]
                 Class     Images  Instances          P          R      mAP50   mAP50-95: 100% 7/7 [00:05<00:00,  1.25it/s]
                   all        200        400      0.981      0.965 

## Medium

In [ ]:
!python train.py --img 640 --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --weights yolov5m.pt --patience 20 --cache

train: weights=yolov5m.pt, cfg=, data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=300, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=20, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
remote: Enumerating objects: 17, done.
remote: Counting objects: 100% (17/17), done.
remote: Compressing objects: 100% (10/10), done.
remote: Total 17 (delta 10), reused 14 (delta 7), pack-reused 0
Unpacking objects: 100% (17/17), done.
From https://github.com/ultralytics/yolov5
   7549f58..a9a498a  exp8       -> origin/exp8
github: up to date with https://github.c

In [ ]:
!cp -r "/content/yolov5/runs/train/exp4" "/content/drive/MyDrive/yolo_datasets/Model_sizes_results/medium"

In [ ]:
!python val.py --weights /content/drive/MyDrive/yolo_datasets/Model_sizes_results/medium/exp4/weights/best.pt --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --task test

val: data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, weights=['/content/drive/MyDrive/yolo_datasets/Model_sizes_results/medium/exp4/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

Fusing layers... 
Model summary: 212 layers, 20856975 parameters, 0 gradients, 47.9 GFLOPs
test: Scanning '/content/datasets_Train640_Val160_Test200/AIROGS/test/labels.cache' images and labels... 200 found, 0 missing, 0 empty, 0 corrupt: 100% 200/200 [00:00<?, ?it/s]
                 Class     Images  Instances          P          R      mAP50   mAP50-95: 100% 7/7 [00:07<00:00,  1.03s/it]
                   all        200        400      0.973       0.9

## Extra large

In [ ]:
!python train.py --img 640 --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --weights yolov5x.pt --patience 20 --cache

train: weights=yolov5x.pt, cfg=, data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=300, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=20, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
remote: Enumerating objects: 20, done.
remote: Counting objects: 100% (20/20), done.
remote: Compressing objects: 100% (8/8), done.
remote: Total 20 (delta 12), reused 18 (delta 12), pack-reused 0
Unpacking objects: 100% (20/20), done.
From https://github.com/ultralytics/yolov5
   a9a498a..114bd70  exp8       -> origin/exp8
github: up to date with https://github.co

In [ ]:
!cp -r "/content/yolov5/runs/train/exp5" "/content/drive/MyDrive/yolo_datasets/Model_sizes_results/xl"

In [ ]:
!python val.py --weights /content/drive/MyDrive/yolo_datasets/Model_sizes_results/xl/exp5/weights/best.pt --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --task test

val: data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, weights=['/content/drive/MyDrive/yolo_datasets/Model_sizes_results/xl/exp5/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

Fusing layers... 
Model summary: 322 layers, 86180143 parameters, 0 gradients, 203.8 GFLOPs
test: Scanning '/content/datasets_Train640_Val160_Test200/AIROGS/test/labels.cache' images and labels... 200 found, 0 missing, 0 empty, 0 corrupt: 100% 200/200 [00:00<?, ?it/s]
                 Class     Images  Instances          P          R      mAP50   mAP50-95: 100% 7/7 [00:15<00:00,  2.21s/it]
                   all        200        400       0.98       0.97  

# Tuning batch size small model

## Batch size 8

In [ ]:
!python train.py --img 640 --batch 8 --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --weights yolov5s.pt --patience 10 --cache

train: weights=yolov5s.pt, cfg=, data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=300, batch_size=8, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=10, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl_g

In [ ]:
!python val.py --weights /content/yolov5/runs/train/exp/weights/best.pt --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --task test

val: data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, weights=['/content/yolov5/runs/train/exp/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

Fusing layers... 
Model summary: 157 layers, 7015519 parameters, 0 gradients, 15.8 GFLOPs
test: Scanning '/content/datasets_Train640_Val160_Test200/AIROGS/test/labels' images and labels...200 found, 0 missing, 0 empty, 0 corrupt: 100% 200/200 [00:00<00:00, 327.93it/s]
test: New cache created: /content/datasets_Train640_Val160_Test200/AIROGS/test/labels.cache
                 Class     Images  Instances          P          R      mAP50   mAP50-95: 100% 7/7 [00:05<00:00,  1.31it/s]
          

## Batch size 24

In [ ]:
!python train.py --img 640 --batch 24 --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --weights yolov5s.pt --patience 10 --cache

train: weights=yolov5s.pt, cfg=, data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=300, batch_size=24, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=10, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl_

In [ ]:
!python val.py --weights /content/yolov5/runs/train/exp2/weights/best.pt --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --task test

val: data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, weights=['/content/yolov5/runs/train/exp2/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

Fusing layers... 
Model summary: 157 layers, 7015519 parameters, 0 gradients, 15.8 GFLOPs
test: Scanning '/content/datasets_Train640_Val160_Test200/AIROGS/test/labels.cache' images and labels... 200 found, 0 missing, 0 empty, 0 corrupt: 100% 200/200 [00:00<?, ?it/s]
                 Class     Images  Instances          P          R      mAP50   mAP50-95: 100% 7/7 [00:05<00:00,  1.34it/s]
                   all        200        400      0.974       0.97      0.985       0.76
            op

## Batch size 32

In [ ]:
!python train.py --img 640 --batch 32 --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --weights yolov5s.pt --patience 10 --cache

train: weights=yolov5s.pt, cfg=, data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=300, batch_size=32, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=10, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl_

In [ ]:
!python val.py --weights /content/yolov5/runs/train/exp3/weights/best.pt --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --task test

val: data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, weights=['/content/yolov5/runs/train/exp3/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v6.2-189-g2f1eb21 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

Fusing layers... 
Model summary: 157 layers, 7015519 parameters, 0 gradients, 15.8 GFLOPs
test: Scanning '/content/datasets_Train640_Val160_Test200/AIROGS/test/labels.cache' images and labels... 200 found, 0 missing, 0 empty, 0 corrupt: 100% 200/200 [00:00<?, ?it/s]
                 Class     Images  Instances          P          R      mAP50   mAP50-95: 100% 7/7 [00:05<00:00,  1.30it/s]
                   all        200        400      0.976      0.963      0.977      0.742
            op

# Hyperparameter evolution small model

## Perform hyperparameter evolution

In [ ]:
!python train.py --img 640 --batch 32 --epochs 35 --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --weights yolov5s.pt --patience 10 --cache --evolve 15

train: weights=yolov5s.pt, cfg=, data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=35, batch_size=32, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=15, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=10, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v6.2-190-g7a69035 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl_gam

In [ ]:
!cp -r "/content/yolov5/runs/evolve/exp/hyp_evolve.yaml" "/content/drive/MyDrive/yolo_datasets/hyperparameter_evolution_file"

## Train model with hyperparameters

In [ ]:
!python train.py --img 640 --batch 32 --hyp '/content/drive/MyDrive/yolo_datasets/hyperparameter_evolution_file/hyp_evolve.yaml' --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --weights yolov5s.pt --patience 10 --cache 

train: weights=yolov5s.pt, cfg=, data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, hyp=/content/drive/MyDrive/yolo_datasets/hyperparameter_evolution_file/hyp_evolve.yaml, epochs=300, batch_size=32, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=10, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
remote: Enumerating objects: 16, done.
remote: Counting objects: 100% (16/16), done.
remote: Compressing objects: 100% (7/7), done.
remote: Total 13 (delta 10), reused 9 (delta 6), pack-reused 0
Unpacking objects: 100% (13/13), done.
From https://github.com/ultralytics/yolov5
   e96eedd..9e62507  exp8       -> ori

## Evaluate model trained with tuned hyperparameters

In [ ]:
!python val.py --weights /content/yolov5/runs/train/exp/weights/best.pt --data /content/datasets_Train640_Val160_Test200/AIROGS/data.yaml --task test

val: data=/content/datasets_Train640_Val160_Test200/AIROGS/data.yaml, weights=['/content/yolov5/runs/train/exp/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v6.2-190-g7a69035 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

Fusing layers... 
Model summary: 157 layers, 7009226 parameters, 0 gradients, 15.7 GFLOPs
test: Scanning '/content/datasets_Train640_Val160_Test200/AIROGS/test/labels' images and labels...200 found, 0 missing, 0 empty, 0 corrupt: 100% 200/200 [00:00<00:00, 327.92it/s]
test: New cache created: /content/datasets_Train640_Val160_Test200/AIROGS/test/labels.cache
                 Class     Images  Instances          P          R      mAP50   mAP50-95: 100% 7/7 [00:05<00:00,  1.30it/s]
          

# Unzip directory with images 1000-1999

In [ ]:
!unzip "/content/drive/MyDrive/yolo_datasets/shuffled_square_png_640_1000-1999Images.zip" -d "/content"


Archive:  /content/drive/MyDrive/yolo_datasets/shuffled_square_png_640_1000-1999Images.zip
  inflating: /content/shuffled_square_png_640_1000-1999Images/SHUF01000.png  
  inflating: /content/shuffled_square_png_640_1000-1999Images/SHUF01001.png  
  inflating: /content/shuffled_square_png_640_1000-1999Images/SHUF01002.png  
  inflating: /content/shuffled_square_png_640_1000-1999Images/SHUF01003.png  
  inflating: /content/shuffled_square_png_640_1000-1999Images/SHUF01004.png  
  inflating: /content/shuffled_square_png_640_1000-1999Images/SHUF01005.png  
  inflating: /content/shuffled_square_png_640_1000-1999Images/SHUF01006.png  
  inflating: /content/shuffled_square_png_640_1000-1999Images/SHUF01007.png  
  inflating: /content/shuffled_square_png_640_1000-1999Images/SHUF01008.png  
  inflating: /content/shuffled_square_png_640_1000-1999Images/SHUF01009.png  
  inflating: /content/shuffled_square_png_640_1000-1999Images/SHUF01010.png  
  inflating: /content/shuffled_square_png_640_1000-

# Predict on 1000 images to get extra training data

In [ ]:
!python detect.py --img 640 --weights /content/drive/MyDrive/yolo_datasets/baseline_small_training_set/exp/weights/best.pt --source /content/shuffled_square_png_640_1000-1999Images --save-txt 


detect: weights=['/content/drive/MyDrive/yolo_datasets/baseline_small_training_set/exp/weights/best.pt'], source=/content/shuffled_square_png_640_1000-1999Images, data=data/coco128.yaml, imgsz=[640, 640], conf_thres=0.25, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=True, save_conf=False, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=runs/detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False, vid_stride=1
YOLOv5 🚀 v6.2-186-g7f097dd Python-3.7.14 torch-1.12.1+cu113 CPU

Fusing layers... 
Model summary: 267 layers, 46113663 parameters, 0 gradients, 107.7 GFLOPs
image 1/1000 /content/shuffled_square_png_640_1000-1999Images/SHUF01000.png: 640x640 1 optic_disk, 1 fovea, 1883.0ms
image 2/1000 /content/shuffled_square_png_640_1000-1999Images/SHUF01001.png: 640x640 1 optic_disk, 1 fovea, 1932.5ms
image 3/1000 /content/shuffled_square_png_640_1000-1

## Save predictions

In [ ]:
!zip -r /content/images_1000_predictions.zip /content/yolov5/runs/detect/exp/labels
from google.colab import files

files.download("/content/images_1000_predictions.zip")

  adding: content/yolov5/runs/detect/exp/labels/ (stored 0%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01231.txt (deflated 31%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01376.txt (deflated 37%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01395.txt (deflated 26%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01836.txt (deflated 31%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01390.txt (deflated 32%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01233.txt (deflated 28%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01608.txt (deflated 28%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01688.txt (deflated 26%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01718.txt (deflated 28%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01372.txt (deflated 29%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01928.txt (deflated 29%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01694.txt (deflated 27%)
  adding: conte

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Train YOLOv5s with batch size 32 on 1640 training images

## Unzip training, test, val data

In [ ]:
# Unzip dataset
!unzip "/content/drive/MyDrive/yolo_datasets/datasets_Train1640_Val160_Test200.zip" -d "/content"

Archive:  /content/drive/MyDrive/yolo_datasets/datasets_Train1640_Val160_Test200.zip
   creating: /content/datasets_Train1640_Val160_Test200/AIROGS/
  inflating: /content/datasets_Train1640_Val160_Test200/AIROGS/data.yaml  
   creating: /content/datasets_Train1640_Val160_Test200/AIROGS/test/
   creating: /content/datasets_Train1640_Val160_Test200/AIROGS/test/images/
  inflating: /content/datasets_Train1640_Val160_Test200/AIROGS/test/images/SHUF00800.png  
  inflating: /content/datasets_Train1640_Val160_Test200/AIROGS/test/images/SHUF00801.png  
  inflating: /content/datasets_Train1640_Val160_Test200/AIROGS/test/images/SHUF00802.png  
  inflating: /content/datasets_Train1640_Val160_Test200/AIROGS/test/images/SHUF00803.png  
  inflating: /content/datasets_Train1640_Val160_Test200/AIROGS/test/images/SHUF00804.png  
  inflating: /content/datasets_Train1640_Val160_Test200/AIROGS/test/images/SHUF00805.png  
  inflating: /content/datasets_Train1640_Val160_Test200/AIROGS/test/images/SHUF00806.

In [ ]:
!python train.py --img 640 --batch 32 --data /content/datasets_Train1640_Val160_Test200/AIROGS/data.yaml --weights yolov5s.pt --patience 10 --cache

train: weights=yolov5s.pt, cfg=, data=/content/datasets_Train1640_Val160_Test200/AIROGS/data.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=300, batch_size=32, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=10, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v6.2-190-g7a69035 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl

## Evaluate YOLOv5s batch size 32 with 1640 training images

In [ ]:
!python val.py --weights /content/yolov5/runs/train/exp/weights/best.pt --data /content/datasets_Train1640_Val160_Test200/AIROGS/data.yaml --task test

val: data=/content/datasets_Train1640_Val160_Test200/AIROGS/data.yaml, weights=['/content/yolov5/runs/train/exp/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v6.2-190-g7a69035 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

Fusing layers... 
Model summary: 157 layers, 7015519 parameters, 0 gradients, 15.8 GFLOPs
test: Scanning '/content/datasets_Train1640_Val160_Test200/AIROGS/test/labels' images and labels...200 found, 0 missing, 0 empty, 0 corrupt: 100% 200/200 [00:00<00:00, 356.38it/s]
test: New cache created: /content/datasets_Train1640_Val160_Test200/AIROGS/test/labels.cache
                 Class     Images  Instances          P          R      mAP50   mAP50-95: 100% 7/7 [00:05<00:00,  1.26it/s]
       

# Train final model on 1840 images

## Unzip training and validation data

In [ ]:
!unzip "/content/drive/MyDrive/yolo_datasets/datasets_Train1840_Val160.zip" -d "/content"


Archive:  /content/drive/MyDrive/yolo_datasets/datasets_Train1840_Val160.zip
   creating: /content/datasets_Train1840_Val160/AIROGS/
  inflating: /content/datasets_Train1840_Val160/AIROGS/data.yaml  
   creating: /content/datasets_Train1840_Val160/AIROGS/test/
   creating: /content/datasets_Train1840_Val160/AIROGS/test/images/
   creating: /content/datasets_Train1840_Val160/AIROGS/test/labels/
   creating: /content/datasets_Train1840_Val160/AIROGS/train/
   creating: /content/datasets_Train1840_Val160/AIROGS/train/images/
  inflating: /content/datasets_Train1840_Val160/AIROGS/train/images/SHUF00000.png  
  inflating: /content/datasets_Train1840_Val160/AIROGS/train/images/SHUF00001.png  
  inflating: /content/datasets_Train1840_Val160/AIROGS/train/images/SHUF00002.png  
  inflating: /content/datasets_Train1840_Val160/AIROGS/train/images/SHUF00003.png  
  inflating: /content/datasets_Train1840_Val160/AIROGS/train/images/SHUF00004.png  
  inflating: /content/datasets_Train1840_Val160/AIRO

## Perform training

In [ ]:
!python train.py --img 640 --batch 32 --data /content/datasets_Train1840_Val160/AIROGS/data.yaml --weights yolov5s.pt --patience 20 --cache

train: weights=yolov5s.pt, cfg=, data=/content/datasets_Train1840_Val160/AIROGS/data.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=300, batch_size=32, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, bucket=, cache=ram, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=20, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest
github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v6.2-190-g7a69035 Python-3.7.14 torch-1.12.1+cu113 CUDA:0 (Tesla T4, 15110MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl_gamma=0

## Save weights final model 

In [ ]:
# Save results
!cp -r "/content/yolov5/runs/train/exp" "/content/drive/MyDrive/yolo_datasets/final_model"

# Inference final model on 15000 images used for training vision transformer

### Unzip the folder with 15000 images

In [ ]:
# Unzip folder with all the images
!unzip "/content/drive/MyDrive/shuffled_square_png_640.zip" -d "/content" 

Streaminguitvoer ingekort tot de laatste 5000 regels.
  inflating: /content/shuffled_square_png_640/SHUF10000.png  
  inflating: /content/shuffled_square_png_640/SHUF10001.png  
  inflating: /content/shuffled_square_png_640/SHUF10002.png  
  inflating: /content/shuffled_square_png_640/SHUF10003.png  
  inflating: /content/shuffled_square_png_640/SHUF10004.png  
  inflating: /content/shuffled_square_png_640/SHUF10005.png  
  inflating: /content/shuffled_square_png_640/SHUF10006.png  
  inflating: /content/shuffled_square_png_640/SHUF10007.png  
  inflating: /content/shuffled_square_png_640/SHUF10008.png  
  inflating: /content/shuffled_square_png_640/SHUF10009.png  
  inflating: /content/shuffled_square_png_640/SHUF10010.png  
  inflating: /content/shuffled_square_png_640/SHUF10011.png  
  inflating: /content/shuffled_square_png_640/SHUF10012.png  
  inflating: /content/shuffled_square_png_640/SHUF10013.png  
  inflating: /content/shuffled_square_png_640/SHUF10014.png  
  inflating: /co

### Predict coordinates optic disk and fovea

In [ ]:
!python detect.py --img 640 --weights /content/drive/MyDrive/yolo_datasets/final_model/exp/weights/best.pt --source /content/shuffled_square_png_640 --save-txt --save-conf

Streaminguitvoer ingekort tot de laatste 5000 regels.
image 10004/15000 /content/shuffled_square_png_640/SHUF10003.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 10005/15000 /content/shuffled_square_png_640/SHUF10004.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 10006/15000 /content/shuffled_square_png_640/SHUF10005.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 10007/15000 /content/shuffled_square_png_640/SHUF10006.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 10008/15000 /content/shuffled_square_png_640/SHUF10007.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 10009/15000 /content/shuffled_square_png_640/SHUF10008.png: 640x640 1 optic_disk, 12.7ms
image 10010/15000 /content/shuffled_square_png_640/SHUF10009.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 10011/15000 /content/shuffled_square_png_640/SHUF10010.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 10012/15000 /content/shuffled_square_png_640/SHUF10011.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 10013/15000 /

## Zip file with predictions 15000 images

In [ ]:
!zip -r /content/labels_150000_predictions.zip /content/yolov5/runs/detect/exp/labels


Streaminguitvoer ingekort tot de laatste 5000 regels.
  adding: content/yolov5/runs/detect/exp/labels/SHUF14338.txt (deflated 34%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF02517.txt (deflated 35%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF02528.txt (deflated 34%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF14194.txt (deflated 33%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF06462.txt (deflated 34%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF09731.txt (deflated 33%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF10994.txt (deflated 31%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF01214.txt (deflated 33%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF13178.txt (deflated 37%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF10278.txt (deflated 33%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF12407.txt (deflated 35%)
  adding: content/yolov5/runs/detect/exp/labels/SHUF06467.txt (deflated 30%)
  adding: content/yolo

## Download zip with predictions 15000 images

In [ ]:
from google.colab import files
files.download("/content/labels_150000_predictions.zip")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Inference final model on 10000 test images

### Unzip the folder with 10000 images

In [ ]:
# Unzip folder with all the test images
!unzip "/content/drive/MyDrive/shuffled_square_png_640_test.zip" -d "/content" 

Streaminguitvoer ingekort tot de laatste 5000 regels.
  inflating: /content/shuffled_square_png_640_test/TEST05000.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05001.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05002.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05003.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05004.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05005.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05006.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05007.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05008.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05009.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05010.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05011.jpg.png  
  inflating: /content/shuffled_square_png_640_test/TEST05012.jpg.png  
  inflating: /content/s

### Predict coordinates optic disk and fovea

In [ ]:
!python detect.py --img 640 --weights /content/drive/MyDrive/yolo_datasets/final_model/exp/weights/best.pt --source /content/shuffled_square_png_640_test --save-txt --save-conf

Streaminguitvoer ingekort tot de laatste 5000 regels.
image 5004/10000 /content/shuffled_square_png_640_test/TEST05003.jpg.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 5005/10000 /content/shuffled_square_png_640_test/TEST05004.jpg.png: 640x640 1 optic_disk, 1 fovea, 12.8ms
image 5006/10000 /content/shuffled_square_png_640_test/TEST05005.jpg.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 5007/10000 /content/shuffled_square_png_640_test/TEST05006.jpg.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 5008/10000 /content/shuffled_square_png_640_test/TEST05007.jpg.png: 640x640 1 optic_disk, 1 fovea, 12.8ms
image 5009/10000 /content/shuffled_square_png_640_test/TEST05008.jpg.png: 640x640 1 optic_disk, 1 fovea, 12.9ms
image 5010/10000 /content/shuffled_square_png_640_test/TEST05009.jpg.png: 640x640 1 optic_disk, 1 fovea, 12.7ms
image 5011/10000 /content/shuffled_square_png_640_test/TEST05010.jpg.png: 640x640 1 optic_disk, 1 fovea, 12.8ms
image 5012/10000 /content/shuffled_square_png_640_

## Zip file with predictions 10000 test images

In [ ]:
!zip -r /content/labels_100000_predictions_test.zip /content/yolov5/runs/detect/exp/labels


Streaminguitvoer ingekort tot de laatste 5000 regels.
  adding: content/yolov5/runs/detect/exp/labels/TEST01966.jpg.txt (deflated 34%)
  adding: content/yolov5/runs/detect/exp/labels/TEST02547.jpg.txt (deflated 34%)
  adding: content/yolov5/runs/detect/exp/labels/TEST03819.jpg.txt (deflated 35%)
  adding: content/yolov5/runs/detect/exp/labels/TEST05316.jpg.txt (deflated 35%)
  adding: content/yolov5/runs/detect/exp/labels/TEST09379.jpg.txt (deflated 33%)
  adding: content/yolov5/runs/detect/exp/labels/TEST06552.jpg.txt (deflated 33%)
  adding: content/yolov5/runs/detect/exp/labels/TEST04994.jpg.txt (deflated 38%)
  adding: content/yolov5/runs/detect/exp/labels/TEST01331.jpg.txt (deflated 34%)
  adding: content/yolov5/runs/detect/exp/labels/TEST05156.jpg.txt (deflated 36%)
  adding: content/yolov5/runs/detect/exp/labels/TEST06963.jpg.txt (deflated 36%)
  adding: content/yolov5/runs/detect/exp/labels/TEST05162.jpg.txt (deflated 34%)
  adding: content/yolov5/runs/detect/exp/labels/TEST042

## Download zip with predictions 10000 test images

In [ ]:
from google.colab import files
files.download("/content/labels_100000_predictions_test.zip")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>